In [1]:
import pandas as pd
import geopandas as gpd
from shapely import wkt
import plotly.express as px
import folium

CENTER_BARCELONA = {"lat": 41.3951, "lon": 2.1734}

def convert_wkt_to_geometry(df: pd.DataFrame, wkt_column: str) -> gpd.GeoDataFrame:
    # Convert the GEOM_WKT column to geometry
    df['geometry'] = df[wkt_column].apply(wkt.loads)

    # Convert the DataFrame to a GeoDataFrame
    return gpd.GeoDataFrame(df.drop(wkt_column, axis='columns'), geometry='geometry')

In [2]:
DATA_PATH = "../../../data/"

gdfs = [
    pd.read_csv(
        DATA_PATH + "air_quality/2023/2023_tramer_no2_mapa_qualitat_aire_bcn.csv"
    )
    .rename(columns={"Rang": "NO2"})
    .astype({"NO2": "category"}),
    pd.read_csv(
        DATA_PATH + "air_quality/2023/2023_tramer_pm2-5_mapa_qualitat_aire_bcn.csv"
    )
    .rename(columns={"Rang": "PM2_5"})
    .astype({"PM2_5": "category"}),
    pd.read_csv(
        DATA_PATH + "air_quality/2023/2023_tramer_pm10_mapa_qualitat_aire_bcn.csv"
    )
    .rename(columns={"Rang": "PM10"})
    .astype({"PM10": "category"}),
]

gdfs = [convert_wkt_to_geometry(gdf, "GEOM_WKT") for gdf in gdfs]
gdf = gdfs[0][["TRAM", "geometry"]]
for temp_gdf in gdfs:
    gdf = gdf.merge(temp_gdf.drop(columns=["geometry"]), on="TRAM")

gdf["NO2"] = gdf["NO2"].cat.reorder_categories(
    [
        "10-20 µg/m³",
        "20-30 µg/m³",
        "30-40 µg/m³",
        "40-50 µg/m³",
        "50-60 µg/m³",
        "60-70 µg/m³",
        ">70 µg/m³",
    ],
    ordered=True,
)

gdf["PM2_5"] = gdf["PM2_5"].cat.reorder_categories(
    ["5-10 µg/m³", "10-15 µg/m³", "15-20 µg/m³", "20-25 µg/m³", "25-30 µg/m³"],
    ordered=True,
)

gdf["PM10"] = gdf["PM10"].cat.reorder_categories(
    [
        "<=15 µg/m³",
        "15-20 µg/m³",
        "20-25 µg/m³",
        "25-30 µg/m³",
        "30-35 µg/m³",
        "35-40 µg/m³",
        "> 40 µg/m³",
    ],
    ordered=True,
)

gdf: gpd.GeoDataFrame = gdf.set_crs(epsg=25831).to_crs(epsg=4326)

In [11]:
def map_air_quality(gdf: gpd.GeoDataFrame, gdf_json: str, polluant: str):
    map = folium.Map(
        location=list(CENTER_BARCELONA.values()),
        tiles="CartoDB Positron",
        zoom_start=12.3,
        prefer_canvas=True,
    )

    # Define a color map for NO2 levels
    color_map = dict(zip(gdf[polluant].cat.categories, px.colors.sequential.Plasma_r))

    def style_function(feature):
        return {
            "fillColor": color_map.get(feature["properties"][polluant], "gray"),
            "color": color_map.get(feature["properties"][polluant], "gray"),
            "weight": 2,
            "fillOpacity": 0.6,
        }

    folium.GeoJson(
        gdf_json,
        name="Air Quality",
        tooltip=folium.GeoJsonTooltip(
            fields=[polluant], aliases=[polluant.replace("_", ".")]
        ),
        style_function=style_function,
    ).add_to(map)

    # Add legend
    legend_html = f"""
    <div style="position: fixed; 
                top: 10px; left: 50px; 
                border: 1px solid grey; border-radius: 5px; padding: 1px 3px;
                background-color:white;
                z-index:9999; font-size:18px;
                ">
        <b>Carte de Barcelone des niveaux de {polluant.replace("_", ".")}</b>
    </div>
    <div style="position: fixed; 
                top: 50px; right: 50px; width: 130px; height: {35 + len(gdf[polluant].cat.categories) * 20}px; 
                border:2px solid grey; z-index:9999; font-size:14px;
                background-color:white;
                padding: 5px 10px;
                ">
        <b>{polluant.replace("_", ".")}</b><br>
        {'<br>'.join(f'<i style="background:{color_map[cat]}">&nbsp;&nbsp;&nbsp;&nbsp;</i> {cat}' for cat in gdf[polluant].cat.categories)}<br>
    </div>
    """

    map.get_root().html.add_child(folium.Element(legend_html))

    return map

polluant = "PM2_5"
map = map_air_quality(gdf, gdf.to_json(), polluant)
map.save(f"air_quality_{polluant}.html")

In [9]:
open("air_quality_NO2.html", "r", encoding="utf-8").read()

'<!DOCTYPE html>\n<html>\n<head>\n    \n    <meta http-equiv="content-type" content="text/html; charset=UTF-8" />\n    \n        <script>\n            L_NO_TOUCH = false;\n            L_DISABLE_3D = false;\n        </script>\n    \n    <style>html, body {width: 100%;height: 100%;margin: 0;padding: 0;}</style>\n    <style>#map {position:absolute;top:0;bottom:0;right:0;left:0;}</style>\n    <script src="https://cdn.jsdelivr.net/npm/leaflet@1.9.3/dist/leaflet.js"></script>\n    <script src="https://code.jquery.com/jquery-1.12.4.min.js"></script>\n    <script src="https://cdn.jsdelivr.net/npm/bootstrap@5.2.2/dist/js/bootstrap.bundle.min.js"></script>\n    <script src="https://cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.js"></script>\n    <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/leaflet@1.9.3/dist/leaflet.css"/>\n    <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/bootstrap@5.2.2/dist/css/bootstrap.min.css"/>\n    <link rel